<a href="https://colab.research.google.com/github/santarabantoosoo/semantic_song_search/blob/main/fine_tuning_pairs.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Aim

> In this notebook I am using the song pairs from the 1 Million dataset. However, in this trial, I am not using the score. 
I will use only songs with similarity score > 0.7. 
In a future notebook, I am planning to use the full dataset with scores. 

Based on this tutorial, Thanks to Shea, Training Sentence Transformers with MNR Loss | Pinecone
https://www.pinecone.io/learn/fine-tune-sentence-transformers-mnr/#fast-fine-tuning


When fine-tuning with MNR loss, we will be dropping all rows with neutral or contradiction labels — keeping only the positive entailment pairs.

We will be feeding sentence A (the premise, known as the anchor) followed by sentence B (the hypothesis, when the label is 0, this is called the positive) into BERT on each step. Unlike softmax loss, we do not use the label feature.

## Semantic Song Search: Fine-Tune Base Model

In [1]:
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


In [2]:
!pip install sentence_transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 85 kB 3.3 MB/s 
     |████████████████████████████████| 5.8 MB 10.5 MB/s 
     |████████████████████████████████| 1.3 MB 56.1 MB/s 
     |████████████████████████████████| 182 kB 65.7 MB/s 
     |████████████████████████████████| 7.6 MB 52.5 MB/s 
  Created wheel for sentence-transformers: filename=sentence_transformers-2.2.2-py3-none-any.whl size=125938 sha256=12b8a3b20e3c577a1587f247e15b71b0465da290f10f91bfd72d9208baab7960
  Stored in directory: /root/.cache/pip/wheels/5e/6f/8c/d88aec621f3f542d26fac0342bef5e693335d125f4e54aeffe
Successfully built sentence-transformers


In [3]:
from sentence_transformers import SentenceTransformer, InputExample
from tqdm.auto import tqdm  # progress bar

import pandas as pd
import numpy as np

### Data Prep

In [4]:
from google.colab import files
files.upload()

Saving song_pairs_lyrics.csv to song_pairs_lyrics.csv


{'song_pairs_lyrics.csv': b'track1_title,track1_artist_name,track2_title,track2_artist_name,lyrics_x,lyrics_y,score\nWe Will Rock You,Queen,Walk This Way,Aerosmith,"\nBuddy, you\'re a boy, make a big noise\nPlaying in the street\nGonna be a big man someday\nYou got mud on your face\nYou big disgrace\nKicking your can\nAll over the place, singing\n\n\nWe will, we will rock you\nWe will, we will rock you\n\n\nBuddy, you\'re a young man, hard man\nShouting in the street\nGonna take on the world someday\nYou got blood on your face\nYou big disgrace\nWaving your banner\nAll over the place\n\nWe will, we will rock you (Sing it out)\nWe will, we will rock you\n\n\nBuddy, you\'re an old man, poor man\nPleading with your eyes\nGonna make you some peace someday\nYou got mud on your face\nBig disgrace\nSomebody better put you back\nInto your place\n\n\nWe will, we will rock you, sing it\nWe will, we will rock you, everybody\nWe will, we will rock you, hmm\nWe will, we will rock you, alright\n\n",

In [133]:
pairs = pd.read_csv("song_pairs_lyrics.csv")

Removing duplicate values and \n

In [156]:
pairs['lyrics_x']=pairs['lyrics_x'].apply(lambda x: ', '.join(set([y.strip() for y in x.split('\n')])))
pairs['lyrics_y']=pairs['lyrics_y'].apply(lambda x: ', '.join(set([y.strip() for y in x.split('\n')])))


<ipython-input-156-7f4e3fb2c930>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pairs['lyrics_x']=pairs['lyrics_x'].apply(lambda x: ', '.join(set([y.strip() for y in x.split('\n')])))
<ipython-input-156-7f4e3fb2c930>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pairs['lyrics_y']=pairs['lyrics_y'].apply(lambda x: ', '.join(set([y.strip() for y in x.split('\n')])))


In [162]:
pairs.head()

track1_title track1_artist_name        track2_title  \
2                  Love Me      Justin Bieber  Common Denominator   
5                 One Time      Justin Bieber       Favorite Girl   
6           I Got You Babe       Sonny & Cher    The Beat Goes On   
7                     Home    LCD Soundsystem             Pow Pow   
8  The Purple People Eater        Sheb Wooley        Witch Doctor   

  track2_artist_name                                           lyrics_x  \
2      Justin Bieber  , I guess I'm just a sucker for love, And ever...   
5      Justin Bieber  , I'ma tell you one time (Girl, Hey, I'ma tell...   
6       Sonny & Cher  , I got you babe, you're a clown, I got you ba...   
7    LCD Soundsystem  , Yeah, a few make sure that you get home, And...   
8      David Seville  , Sure looks strange to me (One horn?), What a...   

                                            lyrics_y     score  
2  , Between me and love, you're the common denom...  0.845078  
5  , Adore you, girl, I want you, The coolest gir...  0.949430  
6  , The cars keep a-going faster all the time, L...  1.000000  
7  , (The return of the police), It goes pow, And...  0.963016  
8  , I told the witch doctor you didn't love me n...  1.000000

In [163]:
pairs = pairs.query('score > 0.7')

In [164]:
pairs.shape

(1037, 7)

In [165]:
pairs

track1_title    track1_artist_name        track2_title  \
2                        Love Me         Justin Bieber  Common Denominator   
5                       One Time         Justin Bieber       Favorite Girl   
6                 I Got You Babe          Sonny & Cher    The Beat Goes On   
7                           Home       LCD Soundsystem             Pow Pow   
8        The Purple People Eater           Sheb Wooley        Witch Doctor   
...                          ...                   ...                 ...   
1482                       Naomi    Neutral Milk Hotel           April 8th   
1485                    Hey Mama            Kanye West         Celebration   
1486               The Wine Song        The Cat Empire       The Lost Song   
1488  Never Ending Math Equation          Modest Mouse               Broke   
1489                  I Can Talk  Two Door Cinema Club       What You Know   

        track2_artist_name                                           lyrics_x  \
2            Justin Bieber  , I guess I'm just a sucker for love, And ever...   
5            Justin Bieber  , I'ma tell you one time (Girl, Hey, I'ma tell...   
6             Sonny & Cher  , I got you babe, you're a clown, I got you ba...   
7          LCD Soundsystem  , Yeah, a few make sure that you get home, And...   
8            David Seville  , Sure looks strange to me (One horn?), What a...   
...                    ...                                                ...   
1482    Neutral Milk Hotel  , So pretty, so pretty, I'm tasting Naomi's pe...   
1485            Kanye West  , I know I act a fool but, you ain't gotta wor...   
1486        The Cat Empire  , Let's have some, Water we're desperately try...   
1488          Modest Mouse  , Well, they look so alone, And, Infinity spir...   
1489  Two Door Cinema Club  , Now I can talk, ah-ah-oh, Now I can talk, ah...   

                                               lyrics_y     score  
2     , Between me and love, you're the common denom...  0.845078  
5     , Adore you, girl, I want you, The coolest gir...  0.949430  
6     , The cars keep a-going faster all the time, L...  1.000000  
7     , (The return of the police), It goes pow, And...  0.963016  
8     , I told the witch doctor you didn't love me n...  1.000000  
...                                                 ...       ...  
1482  , Just late night television, Offer up your st...  0.974651  
1485  , 'Cause now y'all know what this is, Right no...  0.987487  
1486  , They walked away they dressed in black they ...  0.933645  
1488  , No way, no way, that's right, that's right, ...  0.903929  
1489  , To realise it's right before my eyes, I woul...  0.973110  

[1037 rows x 7 columns]

Since we will later use bert-base-uncasesd, I will lower case the lyrics now 

In [166]:
!pip install datasets

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [167]:
pairs = pairs.dropna(subset = ['lyrics_x', 'lyrics_y'])

In [168]:
from datasets import Dataset
dataset = Dataset.from_pandas(pairs)

In [169]:
dataset.set_format(type='torch', output_all_columns=True)

In [170]:
from sentence_transformers import InputExample
from tqdm.auto import tqdm  # so we see progress bar

train_samples = []
for row in tqdm(dataset):
    train_samples.append(InputExample(
        texts=[row['lyrics_x'], row['lyrics_y']]
    ))

  0%|          | 0/1037 [00:00<?, ?it/s]

In [171]:
from sentence_transformers import datasets

batch_size = 32

loader = datasets.NoDuplicatesDataLoader(
    train_samples, batch_size=batch_size)

In [175]:
from sentence_transformers import models, SentenceTransformer

model = SentenceTransformer('all-MiniLM-L12-v2')


model

TypeError: ignored

In [173]:
from sentence_transformers import losses

loss = losses.MultipleNegativesRankingLoss(model)

In [174]:
epochs = 3
warmup_steps = int(len(loader) * epochs * 0.1)

model.fit(
    train_objectives=[(loader, loss)],
    epochs=epochs,
    warmup_steps=warmup_steps,
    output_path='./sbert_test_mnr2',
    show_progress_bar=True
)  # I set 'show_progress_bar=False' as it printed every step
#    on to a new line

Epoch:   0%|          | 0/3 [00:00<?, ?it/s]

Iteration:   0%|          | 0/32 [00:00<?, ?it/s]

Iteration:   0%|          | 0/32 [00:00<?, ?it/s]

Iteration:   0%|          | 0/32 [00:00<?, ?it/s]